# Imports

In [1]:
import pandas as pd
import os
import io
from utils import read_file
from utils import convert_to_unsigned_np
from PIL import Image
import numpy as np
from scipy import signal 
import matplotlib as mpl 
import matplotlib.pyplot as plt 
import requests  # pip install requests 
import sys
import numpy
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier as RF
import scipy
import torch
from utils import Conv
from utils import make_conv_feat
import subprocess

#/data/isip/www/isip/courses/temple/ece_8527/exams/current/exam_04/results/auchincloss_mary

# variable names

In [2]:
DIR = "/data/isip/www/isip/courses/temple/ece_8527/resources/data/set_15/lists"
N = 99487


# Data Loading

### Labels

In [3]:
training_dir = "data_train_healthy.csv"
training_path = os.path.join(DIR,training_dir)
df_train_healthy = pd.read_csv(training_path)

training_dir = "data_train_unhealthy.csv"
training_path = os.path.join(DIR,training_dir)
df_train_unhealthy = pd.read_csv(training_path)

dev_dir = "data_dev_healthy.csv"
dev_path = os.path.join(DIR,dev_dir)
df_dev_healthy = pd.read_csv(dev_path)

dev_dir = "data_dev_unhealthy.csv"
dev_path = os.path.join(DIR,dev_dir)
df_dev_unhealthy = pd.read_csv(dev_path)



In [4]:
df_train_unhealthy.mean(axis=0)

1dAVb    0.178496
RBBB     0.355484
LBBB     0.178878
SB       0.183853
AF       0.209394
ST       0.178496
dtype: float64

In [4]:
len(df_train_unhealthy)

99487

### Features

In [5]:
train_unhealthy_list = read_file(os.path.join(DIR,"data_train_unhealthy.list"))
train_healthy_list = read_file(os.path.join(DIR,"data_train_healthy.list"))
dev_unhealthy_list = read_file(os.path.join(DIR,"data_dev_unhealthy.list"))
dev_healthy_list = read_file(os.path.join(DIR,"data_dev_healthy.list"))

train_unhealthy_list= train_unhealthy_list.strip().split("\n") #file names - strip gets rid of blank space - split turns it into a list of strings
assert len(train_unhealthy_list) == df_train_unhealthy.shape[0], "train data not right shape"

train_healthy_list= train_healthy_list.strip().split("\n")
assert len(train_healthy_list) == df_train_healthy.shape[0], "train data not right shape"

dev_unhealthy_list= dev_unhealthy_list.strip().split("\n")
assert len(dev_unhealthy_list) == df_dev_unhealthy.shape[0], "train data not right shape"

dev_healthy_list= dev_healthy_list.strip().split("\n")
assert len(dev_healthy_list) == df_dev_healthy.shape[0], "train data not right shape"

In [6]:
#train_unhealthy_array = [np.frombuffer(read_file(x),dtype=np.short).reshape((-1,8)) for x in train_unhealthy_list]
#train_healthy_array = [np.frombuffer(read_file(x),dtype=np.short).reshape((-1,8)) for x in train_healthy_list]\

# read in to np arrays from bytes

train_unhealthy_array = [np.frombuffer(read_file(x),dtype=np.short).reshape((-1,8)) for j,x in enumerate(train_unhealthy_list)] #reading in .dat to list of arrays
train_healthy_array = [np.frombuffer(read_file(x),dtype=np.short).reshape((-1,8)) for j,x in enumerate(train_healthy_list)]

In [7]:
print(len(train_unhealthy_array))

99487


## Data processing

In [8]:
#train_healthy_array 
#train_unhealthy_array 

#seperate the channels and turn list of arrays into single array
#first dimension is the data 
#second dimension is the time
#3rd dimension is channels 

healthytemp = np.stack(train_healthy_array, axis = 2).transpose((2,0,1))
unhealthytemp = np.stack(train_unhealthy_array, axis = 2).transpose((2,0,1))

X = np.concatenate([healthytemp,unhealthytemp], axis = 0)
#X = unhealthytemp
X.shape


(199487, 2200, 8)

In [9]:
y = pd.concat([df_train_healthy,df_train_unhealthy]) # process labels 
#y = df_train_unhealthy.head(N)
y.shape

(199487, 6)

In [10]:
X_train = X/255 # normalize data so that the peeks and vallys are from -1 to 1 range
y_train = y


In [11]:
X = 0

In [ ]:
X_train.shape

y_test.shape

In [22]:
pd.DataFrame(X_train[0]).describe() # each colmn is a channel 


0            1            2            3            4  \
count  2200.000000  2200.000000  2200.000000  2200.000000  2200.000000   
mean     -0.001135     0.001713     0.001194     0.001640     0.007725   
std       0.198526     0.070881     0.195002     0.195133     0.452869   
min      -0.184314    -0.082353    -0.894118    -0.874510    -1.996078   
25%      -0.074510    -0.035294     0.023529     0.011765     0.000000   
50%      -0.054902    -0.027451     0.039216     0.023529     0.023529   
75%      -0.031373     0.011765     0.086275     0.086275     0.164706   
max       0.776471     0.356863     0.184314     0.223529     0.654902   

                 5            6            7  
count  2200.000000  2200.000000  2200.000000  
mean      0.003765     0.001528     0.000061  
std       0.177585     0.074449     0.066642  
min      -0.670588    -0.223529    -0.066667  
25%      -0.011765    -0.027451    -0.035294  
50%       0.000000    -0.015686    -0.027451  
75%       0.035294     0.015686     0.007843  
max       0.388235     0.231373     0.341176

# make model   

from torch import nn 
class Model(nn.Module):

    # function: init
    #
    # arguments: input_size - int representing size of input
    #            hidden_size - number of nodes in the hidden layer
    #            num_classes - number of classes to classify
    #
    # return: none
    #
    # This method is the main function.
    #
    def __init__(self):

        # inherit the superclass properties/methods
        #
        super(Model, self).__init__()

        self.conv1 = nn.Conv1d(8, 32, 3,stride = 3) # 8 input channels, 64 output channels, 3x3 kernel, stride 1
        self.maxpool1 = nn.MaxPool1d(3)
        self.relu1 = nn.ReLU()
        self.conv2 = nn.Conv1d(32, 16, 3,stride = 3)
        self.maxpool2 = nn.MaxPool1d(3)
        self.relu2 = nn.ReLU()
    
        self.fc1 = nn.Linear(432, 64)
        self.relu3 = nn.ReLU()
        self.fc2 = nn.Linear(64, 6)

    def forward(self, data):
        data = data.permute(0, 2, 1)

        x = self.conv1(data)
        x = self.maxpool1(x)
        x = self.relu1(x)
        x = self.conv2(x)
        x = self.maxpool2(x)
        x = self.relu2(x)   


        x = x.view(x.size(0), -1)
    
        x = self.fc1(x)
        x = self.relu3(x)
        x = self.fc2(x)

        x = torch.sigmoid(x)
        return x

network doing one layer 


In [12]:
from torch import nn 
class Model(nn.Module):

   
    #
    def __init__(self):

        
        #
        super(Model, self).__init__()

        self.conv1 = nn.Conv1d(8, 64, 3,stride = 2) # 8 input channels, 64 output channels, 3x3 kernel
        self.relu1 = nn.ReLU() # ReLU layer 
        self.conv2 = nn.Conv1d(64, 32, 3,stride = 2)
        self.relu2 = nn.ReLU()
        self.conv3= nn.Conv1d(32, 16, 3,stride = 2 )
        self.relu3 = nn.ReLU()
        self.maxpool = nn.MaxPool1d(2)
        self.fc1 = nn.Linear(2192, 64)
        self.relu4 = nn.ReLU()
        self.fc2 = nn.Linear(64, 32)
        self.relu5 = nn.ReLU()
        self.fc3 = nn.Linear(32, 6)
       
        # 3 convolutions 3 non linearitys 

    def forward(self, data): 
        data = data.permute(0, 2, 1)

        x = self.conv1(data)
        x = self.relu1(x)
        x = self.conv2(x)
        x = self.relu2(x)
        x = self.conv3(x)
        x = self.relu3(x)
        x = self.maxpool(x)
        x = x.view(x.size(0), -1)
        x = self.fc1(x)
        x = self.relu4(x)
        x = self.fc2(x)
        x = self.relu5(x)
        x = self.fc3(x)
        x = torch.sigmoid(x)
        return x

In [13]:
X_train_torch = torch.from_numpy(X_train).float() # make float for pytorch preprossing step 2
y_train_torch = torch.from_numpy(y_train.to_numpy()).float() 

In [14]:
model = Model() # instantiate model
model(X_train_torch[:2]).shape 

torch.Size([2, 6])

In [19]:
optimizer = torch.optim.Adam(model.parameters(), lr=3e-5) 

In [18]:
model = Model()
model.load_state_dict(torch.load("/home/tud03114/finalproject/models/final_model_test6.pth"))

<All keys matched successfully>

In [22]:
# training loop -

# define the loss function

#binary cross entropy loss
def helper_log(x):
    eps = 1e-10
    return torch.log(torch.clamp(x,min=eps,max=1-eps))

def criterion(y_hat, y):
    weights = torch.tensor([.17,.35,.17,.18,.2,.17]).reshape((1,6))

    #loss = y*helper_log(y_hat) + weights*(1-y)*helper_log(1-y_hat)
    #convert na to -100 
    #loss[torch.isnan(loss)] = -100
    loss = (1.0)*y*helper_log(y_hat) + .5*weights*(1-y)*helper_log(1-y_hat)
    tmp = -loss
    return torch.mean(tmp)



num_epochs = 50
batch_size = 128
losses = [ ]

# loop through the num_epochs
for epoch in range(num_epochs):

    # zero the gradients
    optimizer.zero_grad()
    losses = [ ]
    #get batch 
    inds = torch.randperm(X_train.shape[0])
    for i in range(0, len(X_train_torch), batch_size):
        #get a random set of indices of size batch_size
        indices = inds[i:i+batch_size]

        X_batch = X_train_torch[indices]
        y_batch = y_train_torch[indices]

        # forward pass
        outputs = model(X_batch)
        
        # calculate the loss
        loss = criterion(outputs, y_batch)
  
        # backward pass
        loss.backward()

        # optimize
        optimizer.step()

        losses.append(loss.item())
    


    
    # print the loss
    print('Step [{}/{}], Loss: {:.4f}'.format(epoch+1, num_epochs, np.mean(losses)))
 
    if epoch % 25 ==0:
        MODEL_NAME = f"final_model4_{epoch}"

        torch.save(model.state_dict(), f'models/{MODEL_NAME}.pth')


    


Step [1/50], Loss: 0.0094
Step [2/50], Loss: 0.0107
Step [3/50], Loss: 0.0109
Step [4/50], Loss: 0.0102
Step [5/50], Loss: 0.0099
Step [6/50], Loss: 0.0104
Step [7/50], Loss: 0.0102
Step [8/50], Loss: 0.0097
Step [9/50], Loss: 0.0097
Step [10/50], Loss: 0.0098
Step [11/50], Loss: 0.0102
Step [12/50], Loss: 0.0105
Step [13/50], Loss: 0.0098
Step [14/50], Loss: 0.0086
Step [15/50], Loss: 0.0085
Step [16/50], Loss: 0.0094
Step [17/50], Loss: 0.0089
Step [18/50], Loss: 0.0082
Step [19/50], Loss: 0.0087
Step [20/50], Loss: 0.0088
Step [21/50], Loss: 0.0093
Step [22/50], Loss: 0.0096
Step [23/50], Loss: 0.0098
Step [24/50], Loss: 0.0094
Step [25/50], Loss: 0.0095
Step [26/50], Loss: 0.0083
Step [27/50], Loss: 0.0085
Step [28/50], Loss: 0.0085
Step [29/50], Loss: 0.0089
Step [30/50], Loss: 0.0090
Step [31/50], Loss: 0.0087
Step [32/50], Loss: 0.0087
Step [33/50], Loss: 0.0087
Step [34/50], Loss: 0.0080
Step [35/50], Loss: 0.0078
Step [36/50], Loss: 0.0080
Step [37/50], Loss: 0.0088
Step [38/5

In [23]:
MODEL_NAME = "final_model_done"

torch.save(model.state_dict(), f'models/{MODEL_NAME}.pth')

with torch.no_grad(): 
    model.eval()
    
    y_pred = model(torch.tensor(X_test).float())
    #convert to numpy
    y_pred = y_pred.numpy().astype(int)
y_pred.shape

In [24]:
diseases = y.columns.tolist()
print(diseases)


['1dAVb', 'RBBB', 'LBBB', 'SB', 'AF', 'ST']


## Metrics

In [27]:
X_train_torch.shape

torch.Size([199487, 2200, 8])

In [28]:
model = Model()
model.load_state_dict(torch.load("/home/tud03114/finalproject/models/final_model_done.pth"))

#X_train_torch = torch.from_numpy(X).float()
alg = "nn"
data = "train"


In [31]:
#batch eval for memory instead of y_pred = model(torch.tensor(X).float())

with torch.no_grad(): 
    model.eval()

    y_pred = []
    for i in range(0, X_train_torch.shape[0], 128):
        X_batch = torch.tensor(X_train_torch[i:i+batch_size]).float()
        y_pred.append(model(X_batch))
    y_pred = torch.cat(y_pred)

    
    
    #convert to numpy
    y_pred = y_pred.numpy().astype(int)
y_pred.shape  

/tmp/ipykernel_95463/79429147.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  X_batch = torch.tensor(X_train_torch[i:i+batch_size]).float()


(199487, 6)

In [33]:

def produce_hyp_files(y_pred, y_test, alg,data):
  df = pd.DataFrame(columns=diseases)
  for j,dis in enumerate(diseases):
      df[dis] = y_pred[:,j]
  df.to_csv(f'hyps/hyp_{alg}_{data}.csv',index=False)
  y_test.to_csv(f'hyps/ref_{alg}_{data}.csv',index=False)
  #python score.py preds.csv labels.csv

produce_hyp_files(y_pred,y,alg,data)


In [87]:
#df = pd.DataFrame(columns=diseases)
#for j,dis in enumerate(diseases):
#    df[dis] = y_pred[:,j]
#df.to_csv('preds.csv',index=False)
#y_test.to_csv("labels.csv",index=False)
#python score.py preds.csv labels.csv

In [103]:
np.mean(y_pred)

0.24546211031295273

In [34]:
import subprocess
ref = "/home/tud03114/finalproject/hyps/ref_nn_train.csv" 
hyp = "/home/tud03114/finalproject/hyps/hyp_nn_train.csv"

subprocess.run(["python", "score.py",ref,hyp]) 

Metric 1: simple accuracy
 err / acc = 0.4555 / 0.5445

Metric 2: micro accuracy / precision / recall / f1
 micro acc / prec / rec / f1 = 0.9047 / 0.9967 / 0.1074 / 0.1940

Metric 3: macro accuracy / precision / recall / f1
  [1dAVb] acc / prec / rec / f1 = 0.9302 / 0.9977 / 0.2163 / 0.3555
  [RBBB] acc / prec / rec / f1 = 0.8374 / 0.9993 / 0.0831 / 0.1534
  [LBBB] acc / prec / rec / f1 = 0.9216 / 0.9940 / 0.1215 / 0.2165
  [SB] acc / prec / rec / f1 = 0.9084 / 1.0000 / 0.0011 / 0.0023
  [AF] acc / prec / rec / f1 = 0.9002 / 0.9872 / 0.0445 / 0.0852
  [ST] acc / prec / rec / f1 = 0.9302 / 0.9977 / 0.2163 / 0.3555
 macro acc / prec / rec / f1 = 0.9047 / 0.9960 / 0.1138 / 0.1947



CompletedProcess(args=['python', 'score.py', '/home/tud03114/finalproject/hyps/ref_nn_train.csv', '/home/tud03114/finalproject/hyps/hyp_nn_train.csv'], returncode=0)